# The Battle of the Neighborhoods

For my capstone project, I want to explore the arrondissements and famous landmarks and Foursquare venues of Paris in order to create a travel itinerary which takes into account travel time, must-see attractions, and local hot spots.

#### First, I will install the necessary packages for our analysis

In [1]:
import requests
from bs4 import BeautifulSoup
import csv
import json
import xml
import pandas as pd
import numpy as np

!conda install -c conda-forge folium=0.5.0 --yes
import folium
from folium import plugins

import json
from pprint import pprint

!conda install -c conda-forge geopy --yes 
from geopy.geocoders import Nominatim # module to convert an address into latitude and longitude values

# libraries for displaying images
from IPython.display import Image 
from IPython.core.display import HTML 

# Matplotlib and associated plotting modules
import matplotlib.cm as cm
import matplotlib.colors as colors

# import k-means from clustering stage
from sklearn.cluster import KMeans

import pandas as pd # library for data analsysis
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)

import json # library to handle JSON files
import requests # library to handle requests
from pandas.io.json import json_normalize # tranform JSON file into a pandas dataframe


Solving environment: / 
  - anaconda::ca-certificates-2018.03.07-0, anaconda::certifi-2018.11.29-py37_0, anaconda::openssl-1.1.1a-h1de35cc_0
  - anaconda::ca-certificates-2018.03.07-0, anaconda::openssl-1.1.1a-h1de35cc_0, defaults::certifi-2018.11.29-py37_0
  - anaconda::certifi-2018.11.29-py37_0, anaconda::openssl-1.1.1a-h1de35cc_0, defaults::ca-certificates-2018.03.07-0
  - anaconda::openssl-1.1.1a-h1de35cc_0, defaults::ca-certificates-2018.03.07-0, defaults::certifi-2018.11.29-py37_0
  - anaconda::certifi-2018.11.29-py37_0, defaults::ca-certificates-2018.03.07-0, defaults::openssl-1.1.1a-h1de35cc_0
  - defaults::ca-certificates-2018.03.07-0, defaults::certifi-2018.11.29-py37_0, defaults::openssl-1.1.1a-h1de35cc_0
  - anaconda::ca-certificates-2018.03.07-0, anaconda::certifi-2018.11.29-py37_0, defaults::openssl-1.1.1a-h1de35cc_0
  - anaconda::ca-certificates-2018.03.07-0, defaults::certifi-2018.11.29-py37_0, defaults::openssl-1.1.1a-h1de35ccdone

## Package Plan ##

  environment loc

#### Get the HTML of the entire Wikipedia page of the 20 Arrondissements of Paris as a string

In [2]:
url = requests.get('https://en.wikipedia.org/wiki/Arrondissements_of_Paris#Arrondissements').text

#### Apply Beautiful Soup to make Soup of the URL, then apply Prettify to view the nested tags and look for the tag that contains the table with arrondissement information

In [3]:
soup = BeautifulSoup(url, 'lxml')
print(soup.prettify())

<!DOCTYPE html>
<html class="client-nojs" dir="ltr" lang="en">
 <head>
  <meta charset="utf-8"/>
  <title>
   Arrondissements of Paris - Wikipedia
  </title>
  <script>
   document.documentElement.className = document.documentElement.className.replace( /(^|\s)client-nojs(\s|$)/, "$1client-js$2" );
  </script>
  <script>
   (window.RLQ=window.RLQ||[]).push(function(){mw.config.set({"wgCanonicalNamespace":"","wgCanonicalSpecialPageName":false,"wgNamespaceNumber":0,"wgPageName":"Arrondissements_of_Paris","wgTitle":"Arrondissements of Paris","wgCurRevisionId":882367785,"wgRevisionId":882367785,"wgArticleId":1175882,"wgIsArticle":true,"wgIsRedirect":false,"wgAction":"view","wgUserName":null,"wgUserGroups":["*"],"wgCategories":["Articles with short description","Use dmy dates from March 2016","Arrondissements of Paris","Government of Paris"],"wgBreakFrames":false,"wgPageContentLanguage":"en","wgPageContentModel":"wikitext","wgSeparatorTransformTable":["",""],"wgDigitTransformTable":["",""],"

In [4]:
arrond_table = soup.find("table", class_ = 'wikitable sortable')
arrond_table_rows = arrond_table.find_all('tr')


#### Extract the columns Arrondissement, Name, Area, Population, Density

In [5]:
information = []
for row in arrond_table_rows:
    info = row.text.split('\n')[1:-1]
    information.append(info)

del information[0][1::2] # There are extra column headers "" that we don't need, so delete them    

information

[['Arrondissement (R for Right Bank, L for Left Bank)',
  'Name',
  'Area (in km²)',
  'Population(March 1999 census)',
  'Population(July 2005 estimate)',
  'Density (2005)(in h. per km²)',
  'Peak of population'],
 ['1st (Ie) R',
  'Louvre',
  '1.826\xa0km2 (0.705\xa0sq\xa0mi)',
  '16,888',
  '17,700',
  '9,693',
  'before 1861'],
 ['2nd (IIe) R',
  'Bourse',
  '0.992\xa0km2 (0.383\xa0sq\xa0mi)',
  '19,585',
  '20,700',
  '20,867',
  'before 1861'],
 ['3rd (IIIe) R',
  'Temple',
  '1.171\xa0km2 (0.452\xa0sq\xa0mi)',
  '34,248',
  '35,100',
  '29,974',
  'before 1861'],
 ['4th (IVe) R',
  'Hôtel-de-Ville',
  '1.601\xa0km2 (0.618\xa0sq\xa0mi)',
  '30,675',
  '28,600',
  '17,864',
  'before 1861'],
 ['5th (Ve) L',
  'Panthéon',
  '2.541\xa0km2 (0.981\xa0sq\xa0mi)',
  '58,849',
  '60,600',
  '23,849',
  '1911'],
 ['6th (VIe) L',
  'Luxembourg',
  '2.154\xa0km2 (0.832\xa0sq\xa0mi)',
  '44,919',
  '45,200',
  '20,984',
  '1911'],
 ['7th (VIIe) L',
  'Palais-Bourbon',
  '4.088\xa0km2 (1.578

#### Turn above information into a Pandas dataframe

In [6]:
arrond_df = pd.DataFrame(information[1:], columns=information[0])
# where information[1:] contains each row of neighborhoods
# and columns = information[0] gives the column names

arrond_df.head(25)

Arrondissement (R for Right Bank, L for Left Bank)                 Name  \
0                                          1st (Ie) R               Louvre   
1                                         2nd (IIe) R               Bourse   
2                                        3rd (IIIe) R               Temple   
3                                         4th (IVe) R       Hôtel-de-Ville   
4                                          5th (Ve) L             Panthéon   
5                                         6th (VIe) L           Luxembourg   
6                                        7th (VIIe) L       Palais-Bourbon   
7                                       8th (VIIIe) R               Élysée   
8                                         9th (IXe) R                Opéra   
9                                         10th (Xe) R             Entrepôt   
10                                       11th (XIe) R           Popincourt   
11                                      12th (XIIe) R              Reuilly   
12                                     13th (XIIIe) L             Gobelins   
13                                      14th (XIVe) L         Observatoire   
14                                       15th (XVe) L            Vaugirard   
15                                      16th (XVIe) R                Passy   
16                                     17th (XVIIe) R  Batignolles-Monceau   
17                                    18th (XVIIIe) R     Butte-Montmartre   
18                                      19th (XIXe) R      Buttes-Chaumont   
19                                       20th (XXe) R         Ménilmontant   

                                        Area (in km²)  \
0                             1.826 km2 (0.705 sq mi)   
1                             0.992 km2 (0.383 sq mi)   
2                             1.171 km2 (0.452 sq mi)   
3                             1.601 km2 (0.618 sq mi)   
4                             2.541 km2 (0.981 sq mi)   
5                             2.154 km2 (0.832 sq mi)   
6                             4.088 km2 (1.578 sq mi)   
7                             3.881 km2 (1.498 sq mi)   
8                             2.179 km2 (0.841 sq mi)   
9                             2.892 km2 (1.117 sq mi)   
10                            3.666 km2 (1.415 sq mi)   
11  16.324 km2 (6.303 sq mi)¹6.377 km2 (2.462 sq mi)²   
12                            7.146 km2 (2.759 sq mi)   
13                            5.621 km2 (2.170 sq mi)   
14                            8.502 km2 (3.283 sq mi)   
15  16.305 km2 (6.295 sq mi)³7.846 km2 (3.029 sq mi)4   
16                            5.669 km2 (2.189 sq mi)   
17                            6.005 km2 (2.319 sq mi)   
18                            6.786 km2 (2.620 sq mi)   
19                            5.984 km2 (2.310 sq mi)   

   Population(March 1999 census) Population(July 2005 estimate)  \
0                         16,888                         17,700   
1                         19,585                         20,700   
2                         34,248                         35,100   
3                         30,675                         28,600   
4                         58,849                         60,600   
5                         44,919                         45,200   
6                         56,985                         55,400   
7                         39,314                         38,700   
8                         55,838                         58,500   
9                         89,612                         88,800   
10                       149,102                        152,500   
11                       136,591                        138,300   
12                       171,533                        181,300   
13                       132,844                        134,700   
14                       225,362                        232,400   
15                       161,773                        149,500   
16                       16

In [7]:
# Add a column with just the Arrondissement numbers

arrond_number = ['1st', '2nd', '3rd', '4th', '5th', '6th', '7th', '8th', '9th','10th',
                '11th', '12th', '13th', '14th', '15th', '16th', '17th', '18th', '19th', '20th']

Arr = pd.DataFrame({'Arrondissement': arrond_number})

arrond_df = pd.concat([arrond_df, Arr], axis = 1)

arrond_df.head()

Arrondissement (R for Right Bank, L for Left Bank)            Name  \
0                                         1st (Ie) R          Louvre   
1                                        2nd (IIe) R          Bourse   
2                                       3rd (IIIe) R          Temple   
3                                        4th (IVe) R  Hôtel-de-Ville   
4                                         5th (Ve) L        Panthéon   

             Area (in km²) Population(March 1999 census)  \
0  1.826 km2 (0.705 sq mi)                        16,888   
1  0.992 km2 (0.383 sq mi)                        19,585   
2  1.171 km2 (0.452 sq mi)                        34,248   
3  1.601 km2 (0.618 sq mi)                        30,675   
4  2.541 km2 (0.981 sq mi)                        58,849   

  Population(July 2005 estimate) Density (2005)(in h. per km²)  \
0                         17,700                         9,693   
1                         20,700                        20,867   
2                         35,100                        29,974   
3                         28,600                        17,864   
4                         60,600                        23,849   

  Peak of population Arrondissement  
0        before 1861            1st  
1        before 1861            2nd  
2        before 1861            3rd  
3        before 1861            4th  
4               1911            5th

In [8]:
arrond_df.dtypes

Arrondissement (R for Right Bank, L for Left Bank)    object
Name                                                  object
Area (in km²)                                         object
Population(March 1999 census)                         object
Population(July 2005 estimate)                        object
Density (2005)(in h. per km²)                         object
Peak of population                                    object
Arrondissement                                        object
dtype: object

#### Here's a dataframe of the top Paris architectural and historical landmarks I've gathered manually from the Architecture Digest website.

In [9]:
landmarks = ['Cathédrale Notre-Dame de Paris', 'Arc de Triomphe', 'Centre Pompidou',
             'Sacré-Cœur Basilica', 'Eiffel Tower',
             'The Louvre', 'La Grande Arche', 'Les Invalides', 'Fondation Louis Vuitton',
             'Panthéon', 'Picasso Museum', 'Cinémathèque Française',
             'Opéra Garnier', 'The Grand Palais', 'Hôtel de Ville',
             'Fondation Cartier', 'Jeu de Paume', 'Jardin des Plantes',
             'Fondation Jerôme Seydoux-Pathé', 'Île de la Cité',
             'The Palais de Tokyo', 'Philharmonie de Paris', 'Musée d’Orsay',
             'Palais du Luxembourg', 'Montmartre', 'Champs-Élysées',
             'Palace of Versailles', 'Tuileries Garden', 'Moulin Rouge',
             'Disneyland Paris', 'Place de la Concorde', 'Catacombs of Paris',
             'Rodin Museum', 'Île de la Cité', 'Orangerie Museum', 'Pont des Arts',
             'Île Saint-Louis', 'Place Vendôme', 'Saint-Jacques Tower', 'La Conciergerie',
            ]

landmarks_df = pd.DataFrame({'Landmark': landmarks})


#### I will find each landmark's latitude and longitude information using the Nominatim package. 

In [10]:
def landmark_loc(list_of_landmarks):
    for place in list_of_landmarks:
        address = (place)
        geolocator = Nominatim(user_agent="Paris_explorer")
        location = geolocator.geocode(address)
        latitude = location.latitude
        longitude = location.longitude
        print('{''}, {}, {},'.format(place,latitude,longitude))

landmark_loc(landmarks)

Cathédrale Notre-Dame de Paris, 48.85293695, 2.35005149954546,
Arc de Triomphe, 48.8737791, 2.29503722603767,
Centre Pompidou, 48.8605918, 2.35247431766534,
Sacré-Cœur Basilica, 48.88680575, 2.34301534488351,
Eiffel Tower, 48.8582602, 2.29449905431968,
The Louvre, 48.8611473, 2.33802768704666,
La Grande Arche, 48.8930151, 2.2376206,
Les Invalides, 48.8570374, 2.3118779,
Fondation Louis Vuitton, 48.87665005, 2.26333809580246,
Panthéon, 48.8454189, 2.35258442491778,
Picasso Museum, 41.3851066, 2.18120508674285,
Cinémathèque Française, 48.8369987, 2.38263520273537,
Opéra Garnier, 48.87203085, 2.3317901855896,
The Grand Palais, 48.86616135, 2.31222295966943,
Hôtel de Ville, 43.9492974, 4.80526012041732,
Fondation Cartier, 48.8373182, 2.33193184219906,
Jeu de Paume, 48.8658156, 2.32408776132074,
Jardin des Plantes, 48.8432224, 2.35950895709484,
Fondation Jerôme Seydoux-Pathé, 48.8334765, 2.35490681339522,
Île de la Cité, 48.85470505, 2.3474846899114,
The Palais de Tokyo, 48.8639905, 2.29652

#### I will turn the above information into a dataframe (need to find a way to do this more efficiently)

In [26]:
landmarks_loc = ['Cathédrale Notre-Dame de Paris', 48.85293695, 2.35005149954546,
'Arc de Triomphe', 48.8737791, 2.29503722603767,
'Centre Pompidou', 48.8605918, 2.35247431766534,
'Sacré-Cœur Basilica', 48.88680575, 2.34301534488351,
'Eiffel Tower', 48.8582602, 2.29449905431968,
'The Louvre', 48.8611473, 2.33802768704666,
'La Grande Arche', 48.8930151, 2.2376206,
'Les Invalides', 48.8570374, 2.3118779,
'Fondation Louis Vuitton', 48.87665005, 2.26333809580246,
'Panthéon', 48.8454189, 2.35258442491778,
'Picasso Museum', 41.3851066, 2.18120508674285,
'Cinémathèque Française', 48.8369987, 2.38263520273537,
'Opéra Garnier', 48.87203085, 2.3317901855896,
'The Grand Palais', 48.86616135, 2.31222295966943,
'Hôtel de Ville', 43.9492974, 4.80526012041732,
'Fondation Cartier', 48.8373182, 2.33193184219906,
'Jeu de Paume', 48.8658156, 2.32408776132074,
'Jardin des Plantes', 48.8432224, 2.35950895709484,
'Fondation Jerôme Seydoux-Pathé', 48.8334765, 2.35490681339522,
'Île de la Cité', 48.85470505, 2.3474846899114,
'The Palais de Tokyo', 48.8639905, 2.29652151313114,
'Philharmonie de Paris', 48.89192125, 2.39413864295307,
'Musée d’Orsay', 48.85991785, 2.32658283469656,
'Palais du Luxembourg', 48.84852845, 2.33683647732996,
'Montmartre', 46.8021347, -0.7198939,
'Champs-Élysées', 48.8707573, 2.3053312,
'Palace of Versailles', 48.80442525, 2.1202852709926,
'Tuileries Garden', 48.86366215, 2.32683861305756,
'Moulin Rouge', 48.8840787, 2.3324082,
'Disneyland Paris', 48.8711359, 2.77612651196751,
'Place de la Concorde', 29.9002052, -90.0095146,
'Catacombs of Paris', 48.833964, 2.3324924,
'Rodin Museum', 39.9619295, -75.1739508,
'Île de la Cité', 48.85470505, 2.3474846899114,
'Orangerie Museum', 48.8637655, 2.32266020780693,
'Pont des Arts', 48.8578114, 2.3372459,
'Île Saint-Louis', 48.85161305, 2.35673414953666,
'Place Vendôme', 48.8674634, 2.32942811682519,
'Saint-Jacques Tower', 48.8580032, 2.34892171290132,
'La Conciergerie', 48.8559492, 2.3460263]

landmarks_df = pd.DataFrame(np.array(landmarks_loc).reshape(40, 3), columns = ["Landmark","Latitude","Longitude"])

# Change the latitude and longitude to a float
landmarks_df['Latitude'] = landmarks_df.Latitude.astype(float)
landmarks_df['Longitude'] = landmarks_df.Longitude.astype(float)


#### Get latitude/longitude for each arrondissement

In [52]:
# turn numbered arrondissements into a list
arrond_list = arrond_df['Arrondissement'].unique()
arrond_list

def landmark_loc(list_of_arronds):
    for place in list_of_arronds:
        address = (place + ' Arrondissement')
        geolocator = Nominatim(user_agent="arrond_explorer")
        location = geolocator.geocode(address)
        latitude = location.latitude
        longitude = location.longitude
        print('{}, {}, {},'.format(place,latitude,longitude))

landmark_loc(arrond_list)

1st, 48.8646144, 2.334396,
2nd, 48.868743, 2.341688,
3rd, 48.864212, 2.360936,
4th, 48.8562021, 2.3556193,
5th, 48.8460591, 2.3445228,
6th, 48.8504333, 2.3329507,
7th, 48.8570281, 2.3201953,
8th, 48.8773158, 2.3172611,
9th, 48.876019, 2.339962,
10th, 48.876106, 2.35991,
11th, 48.858416, 2.379703,
12th, 48.8396154, 2.3957517,
13th, 48.8323973, 2.3555829,
14th, 48.8330589, 2.3269591,
15th, 48.8413705, 2.3003827,
16th, 48.8631709, 2.2757648,
17th, 48.8842239, 2.3223639,
18th, 48.8900117, 2.3464668,
19th, 48.889343, 2.38436,
20th, 48.865042, 2.398929,


In [72]:
# turn numbered arrondissements into a list
arrond_list = arrond_df['Arrondissement'].unique()
arrond_list

def landmark_loc(list_of_arronds):
    LL = []
    for place in list_of_arronds:
        address = (place + ' Arrondissement')
        geolocator = Nominatim(user_agent="arrond_explorer")
        location = geolocator.geocode(address)
        latitude = location.latitude
        longitude = location.longitude
        LL.append(place)
        LL.append(latitude)
        LL.append(longitude)
    print(LL)


LL = landmark_loc(arrond_list)

['1st', 48.8646144, 2.334396, '2nd', 48.868743, 2.341688, '3rd', 48.864212, 2.360936, '4th', 48.8562021, 2.3556193, '5th', 48.8460591, 2.3445228, '6th', 48.8504333, 2.3329507, '7th', 48.8570281, 2.3201953, '8th', 48.8773158, 2.3172611, '9th', 48.876019, 2.339962, '10th', 48.876106, 2.35991, '11th', 48.858416, 2.379703, '12th', 48.8396154, 2.3957517, '13th', 48.8323973, 2.3555829, '14th', 48.8330589, 2.3269591, '15th', 48.8413705, 2.3003827, '16th', 48.8631709, 2.2757648, '17th', 48.8842239, 2.3223639, '18th', 48.8900117, 2.3464668, '19th', 48.889343, 2.38436, '20th', 48.865042, 2.398929]


In [76]:
# not sure why the LL above couldn't be reshaped, so copied them below to insert into a dataframe converter

LL = ['1st', 48.8646144, 2.334396, '2nd', 48.868743, 2.341688, '3rd', 48.864212, 2.360936, 
      '4th', 48.8562021, 2.3556193, '5th', 48.8460591, 2.3445228, '6th', 48.8504333, 2.3329507, 
      '7th', 48.8570281, 2.3201953, '8th', 48.8773158, 2.3172611, '9th', 48.876019, 2.339962, 
      '10th', 48.876106, 2.35991, '11th', 48.858416, 2.379703, '12th', 48.8396154, 2.3957517, 
      '13th', 48.8323973, 2.3555829, '14th', 48.8330589, 2.3269591, '15th', 48.8413705, 2.3003827, 
      '16th', 48.8631709, 2.2757648, '17th', 48.8842239, 2.3223639, '18th', 48.8900117, 2.3464668, 
      '19th', 48.889343, 2.38436, '20th', 48.865042, 2.398929]


In [80]:
arrond_LL = pd.DataFrame(np.array(LL).reshape(20,3), columns = ["Arrondissement","Latitude","Longitude"])

# Change the latitude and longitude to a float
arrond_LL['Latitude'] = arrond_LL.Latitude.astype(float)
arrond_LL['Longitude'] = arrond_LL.Longitude.astype(float)

arrond_LL

Arrondissement   Latitude  Longitude
0             1st  48.864614   2.334396
1             2nd  48.868743   2.341688
2             3rd  48.864212   2.360936
3             4th  48.856202   2.355619
4             5th  48.846059   2.344523
5             6th  48.850433   2.332951
6             7th  48.857028   2.320195
7             8th  48.877316   2.317261
8             9th  48.876019   2.339962
9            10th  48.876106   2.359910
10           11th  48.858416   2.379703
11           12th  48.839615   2.395752
12           13th  48.832397   2.355583
13           14th  48.833059   2.326959
14           15th  48.841370   2.300383
15           16th  48.863171   2.275765
16           17th  48.884224   2.322364
17           18th  48.890012   2.346467
18           19th  48.889343   2.384360
19           20th  48.865042   2.398929

#### Next, I will upload the GEO JSON file of Paris and attempt to create a choroplath map

In [12]:
with open('arrondissements_osm_paris.geojson') as file:    
    paris = json.load(file)
    
paris


{'type': 'FeatureCollection',
 'features': [{'type': 'Feature',
   'geometry': {'type': 'MultiPolygon',
    'coordinates': [[[[2.350948, 48.863407],
       [2.350155, 48.86199],
       [2.34459, 48.854052],
       [2.339003, 48.857565],
       [2.339953, 48.858226],
       [2.332909, 48.85935],
       [2.320902, 48.863057],
       [2.325926, 48.869581],
       [2.327989, 48.869929],
       [2.330662, 48.868191],
       [2.350948, 48.863407]]]]},
   'properties': {'cartodb_id': 54,
    'insee': 75101,
    'nom': '1er Arrondissement',
    'wikipedia': 'fr:1er arrondissement de Paris',
    'surf_m2': 1814728}},
  {'type': 'Feature',
   'geometry': {'type': 'MultiPolygon',
    'coordinates': [[[[2.327989, 48.869929],
       [2.340045, 48.871981],
       [2.347892, 48.870675],
       [2.354261, 48.86933],
       [2.350948, 48.863407],
       [2.330662, 48.868191],
       [2.327989, 48.869929]]]]},
   'properties': {'cartodb_id': 7,
    'insee': 75102,
    'nom': '2e Arrondissement',
    'wi

### Exploration of the data
I will explore the data by making
- maps (choropleth, superimposed landmarks etc)
- utilizing Foursquare data to find venues by arrondissement
- cluster by K-Means
- other visualizations (restaurants, museums, cafes etc by arrondissement)


#### Then, I will create a map template of Paris using its latitude/longitude 

In [13]:
address = ('Paris, France')
geolocator = Nominatim(user_agent="Paris_explorer")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('{''}, {}, {},'.format(address,latitude,longitude))

Paris, France, 48.8566101, 2.3514992,


In [469]:
paris_lat = 48.8566101
paris_long = 2.3514992

paris_map = folium.Map(location=[paris_lat, paris_long], zoom_start = 12)
paris_map

#### Generate a map that show the borders of the arrondissement and labels

In [84]:
arronds_map = folium.Map(location = [paris_lat, paris_long], zoom_start = 14)

arronds_map.choropleth(
    geo_data=paris,
    key_on='feature.properties.nom',
    fill_color='PuBu', 
    fill_opacity=0.1, 
    line_opacity=0.8,
)

#add neighborhood markers to the Paris map
for lat, long, arrond in zip(arrond_LL['Latitude'], arrond_LL['Longitude'], 
                                 arrond_LL['Arrondissement']):
    label = '{}'.format(arrond)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, long],
        radius = 7, 
        popup = label,
        color = 'red',
        fill = True,
        fill_color = 'blue',
        fill_opacity = 0.7,
        parse_html = False).add_to(arronds_map)
        
# display map
arronds_map

#### Generate choropleth map using the geo json file and the population information

In [15]:
# make new list so that "nom" in geojson matches the arrond in the data

arrond_new = ['1er Arrondissement', '2e Arrondissement','3e Arrondissement',
             '4e Arrondissement', '5e Arrondissement', '6e Arrondissement', 
             '7e Arrondissement', '8e Arrondissement','9e Arrondissement',
             '10e Arrondissement', '11e Arrondissement', '12e Arrondissement', 
             '13e Arrondissement', '14e Arrondissement', '15e Arrondissement',
             '16e Arrondissement', '17e Arrondissement', '18e Arrondissement', 
             '19e Arrondissement', '20e Arrondissement']

# this is the population list. Was going to take this from the dataframe, but it had commas and was an object.o
population_2005 = [17700, 20700, 35100, 28600, 60600,
45200,55400,38700,58500,88800,152500,138300,181300,134700,
232400,149500,160300,188700,187200,191800]


pop_2005 = pd.DataFrame({'Arrondissement': arrond_new, 'Population': population_2005})


#### Here is a choropleth map of Paris, where darker shades signify a higher Parisan population

In [476]:
Paris_map = folium.Map(location = [paris_lat, paris_long], zoom_start = 14)

Paris_map.choropleth(
    geo_data=paris,
    data=pop_2005,
    columns=['Arrondissement', 'Population'],
    key_on='feature.properties.nom',
    fill_color='Reds', 
    fill_opacity=0.5, 
    line_opacity=0.2,
    legend_name='Population by Arrondissement in Paris 2005'
)


# display map
Paris_map

#### Map of Parisian arrondissement (labeled) along with population information

In [477]:
paris_map_v2 = folium.Map(location = [paris_lat, paris_long], zoom_start = 12)

paris_map_v2.choropleth(
    geo_data=paris,
    data=pop_2005,
    columns=['Arrondissement', 'Population'],
    key_on='feature.properties.nom',
    fill_color='PuBu', 
    fill_opacity=0.5, 
    line_opacity=0.2,
    legend_name='Population by Arrondissement in Paris 2005'
)

#add neighborhood markers to the Paris map
for lat, long, arrond in zip(arrond_LL['Latitude'], arrond_LL['Longitude'], 
                                 arrond_LL['Arrondissement']):
    label = '{}'.format(arrond)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, long],
        radius = 7, 
        popup = label,
        color = 'red',
        fill = True,
        fill_color = 'blue',
        fill_opacity = 0.7,
        parse_html = False).add_to(paris_map_v2)
        

# display map
paris_map_v2

#### Another option for a choroplath map with arrond long/lat points

In [472]:
from folium import IFrame

paris_map_v3 = folium.Map(location = [paris_lat, paris_long], zoom_start = 12)

paris_map_v3.choropleth(
    geo_data=paris,
    data=pop_2005,
    columns=['Arrondissement', 'Population'],
    key_on='feature.properties.nom',
    fill_color='PuBu', 
    fill_opacity=0.5, 
    line_opacity=0.2,
    legend_name='Population by Arrondissement in Paris 2005'
)

#add neighborhood markers to the Paris map
for lat, long, arrond in zip(arrond_LL['Latitude'], arrond_LL['Longitude'], 
                                 arrond_LL['Arrondissement']):
    label = '{}'.format(arrond)
    iframe = folium.IFrame(label, width=700, height=450)
    label = folium.Popup(iframe, parse_html=True)
    folium.CircleMarker(
        [lat, long],
        radius = 7, 
        color = 'red',
        fill = True,
        fill_color = 'blue',
        fill_opacity = 0.7,
        parse_html = False).add_to(paris_map_v3)
        

# display map
paris_map_v3



#### Map of Paris with markers of top tourists landmarks

In [85]:
# create a map of Paris
map_landmarks = folium.Map(location = [paris_lat, paris_long], zoom_start = 10)

map_landmarks.choropleth(
    geo_data=paris,
    key_on='feature.properties.nom',
    fill_color='PuBu', 
    fill_opacity=0.1, 
    line_opacity=0.8,
)

#add neighborhood markers to the Paris map
for lat, long, landmark in zip(landmarks_df['Latitude'], landmarks_df['Longitude'], 
                                 landmarks_df['Landmark']):
    label = '{}'.format(landmark)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, long],
        radius = 7, 
        popup = label,
        color = 'red',
        fill = True,
        fill_color = 'blue',
        fill_opacity = 0.7,
        parse_html = False).add_to(map_landmarks)
        
map_landmarks

#### Map of Paris with landmarks and arrondissements

In [351]:
# create a map of Paris
map_landmarks2 = folium.Map(location = [paris_lat, paris_long], zoom_start = 10)

map_landmarks2.choropleth(
    geo_data=paris,
    data=pop_2005,
    columns=['Arrondissement', 'Population'],
    key_on='feature.properties.nom',
    fill_color='PuBu', 
    fill_opacity=0.1, 
    line_opacity=0.5,
)

#add landmarks markers to the Paris map
for lat, long, landmark in zip(landmarks_df['Latitude'], landmarks_df['Longitude'], 
                                 landmarks_df['Landmark']):
    label = '{}'.format(landmark)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, long],
        radius = 7, 
        popup = label,
        color = 'red',
        fill = True,
        fill_color = 'blue',
        fill_opacity = 0.7,
        parse_html = False).add_to(map_landmarks2)
    
#add neighborhood markers to the Paris map
for lat, long, arrond in zip(arrond_LL['Latitude'], arrond_LL['Longitude'], 
                                 arrond_LL['Arrondissement']):
    label = '{}'.format(arrond)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, long],
        radius = 5, 
        popup = label,
        color = 'white',
        fill = True,
        fill_color = 'green',
        fill_opacity = 0.5,
        parse_html = False).add_to(map_landmarks2)
        
map_landmarks2

#### Let's bring in the Foursquare data

In [123]:
CLIENT_ID = 'NBGXQTF5JJ5EQZHXHXZCG2AABE4C20W5JXQ25XXSXNM34F0C' # your Foursquare ID
CLIENT_SECRET = 'NW2Q1KMTFNFR4EJCCS1W5OUCA5INYO1Z0QPJUG3KOPH2DXJS' # your Foursquare Secret
VERSION = '20180605' # Foursquare API version


#### Now, let's get the top 250 venues from each of the arrondissement with the most landmarks,  the 1st, 4th, 7th, and 8th. From online research, other vistor favorites are the 5th, 18th, 6th, and 3rd arrondissements.

In [102]:
# Make dataframe of the most popular arrondissement


popular_arrond = arrond_LL[arrond_LL['Arrondissement'].isin(
    ['1st', '3rd', '4th', '5th', '6th', '7th', '8th', '18th'])]

popular_arrond

Arrondissement   Latitude  Longitude
0             1st  48.864614   2.334396
2             3rd  48.864212   2.360936
3             4th  48.856202   2.355619
4             5th  48.846059   2.344523
5             6th  48.850433   2.332951
6             7th  48.857028   2.320195
7             8th  48.877316   2.317261
17           18th  48.890012   2.346467

In [93]:
# Example call of 1st arrondissement

arrond_1_lat = arrond_LL.iloc[0,1]

arrond_1_long = arrond_LL.iloc[0,2]

LIMIT = 250

radius = 2000



url1 = 'https://api.foursquare.com/v2/venues/explore?client_id={}&client_secret={}&ll={},{}&v={}&radius={}&limit={}'.format(
    CLIENT_ID, 
    CLIENT_SECRET, 
    arrond_1_lat, 
    arrond_1_long, 
    VERSION, 
    radius, 
    LIMIT)

url1

'https://api.foursquare.com/v2/venues/explore?client_id=NBGXQTF5JJ5EQZHXHXZCG2AABE4C20W5JXQ25XXSXNM34F0C&client_secret=NW2Q1KMTFNFR4EJCCS1W5OUCA5INYO1Z0QPJUG3KOPH2DXJS&ll=48.8646144,2.334396&v=20180605&radius=2000&limit=250'

#### Send the GET request and examine the results

In [94]:
results1 = requests.get(url1).json()
results1

{'meta': {'code': 200, 'requestId': '5c65dc206a60712d371b6bc4'},
 'response': {'suggestedFilters': {'header': 'Tap to show:',
   'filters': [{'name': 'Open now', 'key': 'openNow'}]},
  'headerLocation': 'Palais-Royal',
  'headerFullLocation': 'Palais-Royal, Paris',
  'headerLocationGranularity': 'neighborhood',
  'totalResults': 240,
  'suggestedBounds': {'ne': {'lat': 48.88261441800002,
    'lng': 2.3617071938645045},
   'sw': {'lat': 48.846614381999984, 'lng': 2.3070848061354954}},
  'groups': [{'type': 'Recommended Places',
    'name': 'recommended',
    'items': [{'reasons': {'count': 0,
       'items': [{'summary': 'This spot is popular',
         'type': 'general',
         'reasonName': 'globalInteractionReason'}]},
      'venue': {'id': '4f0b706de5e8207020057ed7',
       'name': 'Sanukiya',
       'location': {'address': "9 rue d'Argenteuil",
        'lat': 48.86471255164696,
        'lng': 2.334059025405792,
        'labeledLatLngs': [{'label': 'display',
          'lat': 48.8

#### Get Foursquare data for most popular arrondissements and their top venues

In [149]:


def getNearbyVenues(names, latitudes, longitudes, radius, LIMIT):
    
    venues_list=[]
    for name, lat, lng in zip(names, latitudes, longitudes):
        print(name)
            
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            LIMIT)
            
        # make the GET request
        results = requests.get(url).json()["response"]['groups'][0]['items']
        
        # return only relevant information for each nearby venue
        venues_list.append([(
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],
            v['venue']['categories'][0]['name']) for v in results])
            

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Arrondissement', 
                  'Arrondissement Latitude', 
                  'Arrondissement Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    
    return(nearby_venues)

In [150]:
popular_arrond_venues = getNearbyVenues(names=popular_arrond['Arrondissement'],
                                   latitudes=popular_arrond['Latitude'],
                                   longitudes=popular_arrond['Longitude'],
                                   radius=2000, LIMIT=300
                                  )


1st
3rd
4th
5th
6th
7th
8th
18th


#### On second thought, I'm going to run the Foursquare gathering data for all of the arrondissement

In [407]:
arrond_venues = getNearbyVenues(names=arrond_LL['Arrondissement'],
                                   latitudes=arrond_LL['Latitude'],
                                   longitudes=arrond_LL['Longitude'],
                                   radius=2000, LIMIT=300
                                  )


1st
2nd
3rd
4th
5th
6th
7th
8th
9th
10th
11th
12th
13th
14th
15th
16th
17th
18th
19th
20th


#### Here's the output from the code above, with 800 venues

In [154]:
print(arrond_venues.shape)
arrond_venues

(2000, 7)


Arrondissement  Arrondissement Latitude  Arrondissement Longitude  \
0               1st                48.864614                  2.334396   
1               1st                48.864614                  2.334396   
2               1st                48.864614                  2.334396   
3               1st                48.864614                  2.334396   
4               1st                48.864614                  2.334396   
5               1st                48.864614                  2.334396   
6               1st                48.864614                  2.334396   
7               1st                48.864614                  2.334396   
8               1st                48.864614                  2.334396   
9               1st                48.864614                  2.334396   
10              1st                48.864614                  2.334396   
11              1st                48.864614                  2.334396   
12              1st                48.864614                  2.334396   
13              1st                48.864614                  2.334396   
14              1st                48.864614                  2.334396   
15              1st                48.864614                  2.334396   
16              1st                48.864614                  2.334396   
17              1st                48.864614                  2.334396   
18              1st                48.864614                  2.334396   
19              1st                48.864614                  2.334396   
20              1st                48.864614                  2.334396   
21              1st                48.864614                  2.334396   
22              1st                48.864614                  2.334396   
23              1st                48.864614                  2.334396   
24              1st                48.864614                  2.334396   
25              1st                48.864614                  2.334396   
26              1st                48.864614                  2.334396   
27              1st                48.864614                  2.334396   
28              1st                48.864614                  2.334396   
29              1st                48.864614                  2.334396   
30              1st                48.864614                  2.334396   
31              1st                48.864614                  2.334396   
32              1st                48.864614                  2.334396   
33              1st                48.864614                  2.334396   
34              1st                48.864614                  2.334396   
35              1st                48.864614                  2.334396   
36              1st                48.864614                  2.334396   
37              1st                48.864614                  2.334396   
38              1st                48.864614                  2.334396   
39              1st                48.864614                  2.334396   
40              1st                48.864614                  2.334396   
41              1st                48.864614                  2.334396   
42              1st                48.864614                  2.334396   
43              1st                48.864614                  2.334396   
44              1st                48.864614                  2.334396   
45              1st                48.864614                  2.334396   
46              1st                48.864614                  2.334396   
47              1st                48.864614                  2.334396   
48              1st                48.864614                  2.334396   
49              1st                48.864614                  2.334396   
50              1st                48.864614                  2.334396   
51              1st                48.864614                  2.334396   
52              1st                48.864614                  2.334396   
53       

#### There are some duplicates of venues, so we will get rid of the duplicates and keep one copy

In [434]:
arrond_venues = arrond_venues.drop_duplicates(subset=['Venue'], keep = 'first')

#### Here's the venues returned by arrondissement

In [435]:
arrond_venues.groupby('Arrondissement').count()


Arrondissement Latitude  Arrondissement Longitude  Venue  \
Arrondissement                                                             
10th                                 23                        23     23   
11th                                 69                        69     69   
12th                                 83                        83     83   
13th                                 87                        87     87   
14th                                 79                        79     79   
15th                                 78                        78     78   
16th                                 94                        94     94   
17th                                 47                        47     47   
18th                                 54                        54     54   
19th                                 94                        94     94   
1st                                  98                        98     98   
20th                                 69                        69     69   
2nd                                  32                        32     32   
3rd                                  84                        84     84   
4th                                  34                        34     34   
5th                                  69                        69     69   
6th                                  28                        28     28   
7th                                  27                        27     27   
8th                                  61                        61     61   
9th                                  39                        39     39   

                Venue Latitude  Venue Longitude  Venue Category  
Arrondissement                                                   
10th                        23               23              23  
11th                        69               69              69  
12th                        83               83              83  
13th                        87               87              87  
14th                        79               79              79  
15th                        78               78              78  
16th                        94               94              94  
17th                        47               47              47  
18th                        54               54              54  
19th                        94               94              94  
1st                         98               98              98  
20th                        69               69              69  
2nd                         32               32              32  
3rd                         84               84              84  
4th                         34               34              34  
5th                         69               69              69  
6th                         28               28              28  
7th                         27               27              27  
8th                         61               61              61  
9th                         39               39              39

#### Next, I'm going to analysize each arrondissement's venues/


In [437]:
# one hot encoding
arrond_onehot = pd.get_dummies(arrond_venues[['Venue Category']], prefix="", prefix_sep="")

# add neighborhood column back to dataframe
arrond_onehot['Arrondissement'] = arrond_venues['Arrondissement'] 

# move neighborhood column to the first column
fixed_columns = [arrond_onehot.columns[-1]] + list(arrond_onehot.columns[:-1])
arrond_onehot = arrond_onehot[fixed_columns]

arrond_onehot.head()


Arrondissement  African Restaurant  American Restaurant  Arepa Restaurant  \
0            1st                   0                    0                 0   
1            1st                   0                    0                 0   
2            1st                   0                    0                 0   
3            1st                   0                    0                 0   
4            1st                   0                    0                 0   

   Argentinian Restaurant  Art Gallery  Art Museum  Arts & Crafts Store  \
0                       0            0           0                    0   
1                       0            0           0                    0   
2                       0            0           0                    0   
3                       0            0           0                    0   
4                       0            0           1                    0   

   Asian Restaurant  Auvergne Restaurant  BBQ Joint  Bagel Shop  Bakery  Bar  \
0                 0                    0          0           0       0    0   
1                 0                    0          0           0       0    0   
2                 0                    0          0           0       0    0   
3                 0                    0          0           0       0    0   
4                 0                    0          0           0       0    0   

   Basketball Court  Basketball Stadium  Basque Restaurant  Bed & Breakfast  \
0                 0                   0                  0                0   
1                 0                   0                  0                0   
2                 0                   0                  0                0   
3                 0                   0                  0                0   
4                 0                   0                  0                0   

   Beer Bar  Beer Garden  Beer Store  Bike Rental / Bike Share  Bistro  \
0         0            0           0                         0       0   
1         0            0           0                         0       0   
2         0            0           0                         0       0   
3         0            0           0                         0       0   
4         0            0           0                         0       0   

   Boat or Ferry  Bookstore  Botanical Garden  Boutique  Boxing Gym  \
0              0          0                 0         0           0   
1              0          0                 0         0           0   
2              0          0                 0         0           0   
3              0          0                 0         0           0   
4              0          0                 0         0           0   

   Brasserie  Brazilian Restaurant  Breakfast Spot  Breton Restaurant  \
0          0                     0               0                  0   
1          0                     0               0                  0   
2          0                     0               0                  0   
3          0                     0               0                  0   
4          0                     0               0                  0   

   Brewery  Bridge  Burger Joint  Butcher  Café  Cambodian Restaurant  Canal  \
0        0       0             0        0     0                     0      0   
1        0       0             0        0     0                     0      0   
2        0       0             0        0     0                     0      0   
3        0       0             0        0     0                     0      0   
4        0       0             0        0     0                     0      0   

   Canal Lock  Candy Store  Cemetery  Ch'ti Restaurant  Champagne Bar  \
0           0            0         0                 0              0   
1           0            0         0                 0              0   
2           0            0         0                 0              0   
3           0            0         0

#### Next, let's group rows by neighborhood and by taking the mean of the frequency of occurrence of each category


In [438]:
arrond_grouped = arrond_onehot.groupby('Arrondissement').mean().reset_index()
arrond_grouped

Arrondissement  African Restaurant  American Restaurant  Arepa Restaurant  \
0            10th            0.000000             0.000000          0.000000   
1            11th            0.000000             0.000000          0.000000   
2            12th            0.000000             0.012048          0.000000   
3            13th            0.000000             0.000000          0.000000   
4            14th            0.000000             0.000000          0.000000   
5            15th            0.000000             0.000000          0.000000   
6            16th            0.000000             0.000000          0.000000   
7            17th            0.000000             0.000000          0.000000   
8            18th            0.000000             0.018519          0.018519   
9            19th            0.000000             0.000000          0.000000   
10            1st            0.000000             0.000000          0.000000   
11           20th            0.014493             0.000000          0.000000   
12            2nd            0.000000             0.000000          0.000000   
13            3rd            0.000000             0.000000          0.000000   
14            4th            0.000000             0.000000          0.000000   
15            5th            0.000000             0.000000          0.000000   
16            6th            0.000000             0.035714          0.000000   
17            7th            0.000000             0.000000          0.000000   
18            8th            0.000000             0.000000          0.000000   
19            9th            0.000000             0.000000          0.000000   

    Argentinian Restaurant  Art Gallery  Art Museum  Arts & Crafts Store  \
0                 0.000000     0.043478    0.000000             0.000000   
1                 0.000000     0.000000    0.014493             0.000000   
2                 0.000000     0.000000    0.000000             0.000000   
3                 0.000000     0.000000    0.000000             0.000000   
4                 0.000000     0.000000    0.012658             0.000000   
5                 0.000000     0.000000    0.000000             0.012821   
6                 0.000000     0.000000    0.042553             0.000000   
7                 0.000000     0.021277    0.000000             0.000000   
8                 0.000000     0.000000    0.000000             0.000000   
9                 0.000000     0.010638    0.000000             0.000000   
10                0.000000     0.020408    0.051020             0.000000   
11                0.000000     0.000000    0.000000             0.000000   
12                0.000000     0.000000    0.031250             0.000000   
13                0.011905     0.023810    0.000000             0.000000   
14                0.000000     0.000000    0.029412             0.000000   
15                0.000000     0.014493    0.014493             0.000000   
16                0.000000     0.035714    0.000000             0.000000   
17                0.000000     0.000000    0.074074             0.000000   
18                0.000000     0.032787    0.016393             0.000000   
19                0.000000     0.000000    0.025641             0.000000   

    Asian Restaurant  Auvergne Restaurant  BBQ Joint  Bagel Shop    Bakery  \
0           0.000000             0.000000   0.000000    0.000000  0.043478   
1           0.014493             0.000000   0.014493    0.000000  0.014493   
2           0.000000             0.000000   0.000000    0.012048  0.048193   
3           0.022989             0.000000   0.000000    0.000000  0.034483   
4           0.000000             0.012658   0.000000    0.000000  0.012658   
5           0.012821             0.000000   0.000000    0.000000  0.064103   
6           0.000000             0.000000   0.000000    0.000000  0.042553   
7           0.000000             0.000000   0.000000    0.000000  0.063830   
8           0.000000   

#### It's hard to see all the frequencies in this table, so I will print the top 10 venues for each neighborhood

In [439]:
num_top_venues = 10

for hood in arrond_grouped['Arrondissement']:
    print("----"+hood+"----")
    temp = arrond_grouped[arrond_grouped['Arrondissement'] == hood].T.reset_index()
    temp.columns = ['venue','freq']
    temp = temp.iloc[1:]
    temp['freq'] = temp['freq'].astype(float)
    temp = temp.round({'freq': 2})
    print(temp.sort_values('freq', ascending=False).reset_index(drop=True).head(num_top_venues))
    print('\n')

----10th----
                  venue  freq
0     French Restaurant  0.13
1           Coffee Shop  0.13
2  Cambodian Restaurant  0.09
3       Thai Restaurant  0.09
4                   Bar  0.09
5                Bakery  0.04
6                Museum  0.04
7             Gastropub  0.04
8            Boxing Gym  0.04
9            Taco Place  0.04


----11th----
                venue  freq
0   French Restaurant  0.14
1            Wine Bar  0.09
2        Cocktail Bar  0.06
3                 Bar  0.06
4              Bistro  0.06
5         Pizza Place  0.04
6          Restaurant  0.03
7  Italian Restaurant  0.03
8      Chocolate Shop  0.01
9     Organic Grocery  0.01


----12th----
                venue  freq
0   French Restaurant  0.07
1                Park  0.05
2              Bakery  0.05
3              Garden  0.04
4               Plaza  0.04
5  Italian Restaurant  0.04
6                 Bar  0.04
7               Hotel  0.04
8     Thai Restaurant  0.02
9         Beer Garden  0.02


----13th-

#### Put the top venues information into a dataframe that's sorted in descending order

In [440]:
def return_most_common_venues(row, num_top_venues):
    row_categories = row.iloc[1:]
    row_categories_sorted = row_categories.sort_values(ascending=False)
    
    return row_categories_sorted.index.values[0:num_top_venues]

#### Create a new dataframe and display the top 10 venues

In [441]:
num_top_venues = 10

indicators = ['st', 'nd', 'rd']

# create columns according to number of top venues
columns = ['Arrondissement']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

# create a new dataframe
arrond_venues_sorted = pd.DataFrame(columns=columns)
arrond_venues_sorted['Arrondissement'] = arrond_grouped['Arrondissement']

for ind in np.arange(arrond_grouped.shape[0]):
    arrond_venues_sorted.iloc[ind, 1:] = return_most_common_venues(arrond_grouped.iloc[ind, :], num_top_venues)

arrond_venues_sorted

Arrondissement 1st Most Common Venue  2nd Most Common Venue  \
0            10th           Coffee Shop      French Restaurant   
1            11th     French Restaurant               Wine Bar   
2            12th     French Restaurant                   Park   
3            13th     French Restaurant  Vietnamese Restaurant   
4            14th     French Restaurant                  Hotel   
5            15th     French Restaurant                  Hotel   
6            16th     French Restaurant                  Hotel   
7            17th     French Restaurant                  Hotel   
8            18th     French Restaurant     Italian Restaurant   
9            19th     French Restaurant             Restaurant   
10            1st                 Hotel                  Plaza   
11           20th                   Bar      French Restaurant   
12            2nd          Cocktail Bar      French Restaurant   
13            3rd     French Restaurant     Italian Restaurant   
14            4th     French Restaurant                  Plaza   
15            5th     French Restaurant                  Plaza   
16            6th     French Restaurant                  Hotel   
17            7th     French Restaurant          Historic Site   
18            8th                 Hotel      French Restaurant   
19            9th     French Restaurant                 Bakery   

   3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
0   Cambodian Restaurant                   Bar       Thai Restaurant   
1                 Bistro                   Bar          Cocktail Bar   
2                 Bakery                 Hotel                 Plaza   
3        Thai Restaurant    Italian Restaurant                  Café   
4    Japanese Restaurant    Italian Restaurant                Bistro   
5                 Bakery                Bistro  Gym / Fitness Center   
6     Italian Restaurant            Art Museum                Bakery   
7                 Bistro                   Bar                Bakery   
8            Pizza Place                   Bar                Bistro   
9              Multiplex   Japanese Restaurant                Bistro   
10         Historic Site     French Restaurant          Cocktail Bar   
11          Cocktail Bar           Pizza Place                Bakery   
12              Wine Bar                 Hotel           Pizza Place   
13             Bookstore                  Café                Bakery   
14          Cocktail Bar   Japanese Restaurant                Museum   
15              Wine Bar                Bistro          Dessert Shop   
16                  Café           Cheese Shop           Coffee Shop   
17                Garden                 Plaza           Pastry Shop   
18   Japanese Restaurant          Gourmet Shop    Italian Restaurant   
19                 Hotel    Italian Restaurant   Indie Movie Theater   

   6th Most Common Venue  7th Most Common Venue   8th Most Common Venue  \
0            Pizza Place     Chinese Restaurant               Gastropub   
1            Pizza Place     Italian Restaurant              Restaurant   
2     Italian Restaurant                    Bar                  Garden   
3                  Hotel                    Bar                  Bakery   
4               Creperie                    Bar            Dessert Shop   
5                  Plaza      Korean Restaurant      Italian Restaurant   
6                  Plaza              Hotel Bar    Gym / Fitness Center   
7     Italian Restaurant                  Plaza                Wine Bar   
8            Music Venue                 Bakery               Wine Shop   
9                   Café           Concert Hall                     Bar   
10            Art Museum               Boutique      Italian Restaurant   
11    Italian Restaurant  Vietnamese Restaurant             Music Venue   
12          Concert Hall    Corsican Restaurant             Candy Store   
13                 Hotel         Clothing Store      

#### Cluster the arrondissements of Paris

In [442]:
# run K-means to cluster the arrondissements into 5 clusters

# set number of clusters
kclusters = 5

arrond_grouped_clustering = arrond_LL.drop('Arrondissement', 1)

# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(arrond_grouped_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_[0:10]

array([0, 0, 2, 2, 3, 3, 3, 0, 0, 2], dtype=int32)

In [445]:
# add clustering labels
#arrond_venues_sorted.insert(0, 'Cluster Label', kmeans.labels_)

arrond_merge = arrond_LL

# merge grouped with data to add latitude/longitude for each arrondissement
arrond_merge = arrond_merge.join(arrond_venues_sorted.set_index('Arrondissement'), on='Arrondissement')

#arrond_merge = arrond_merge.drop('Cluster',1) # accidentally added added another cluster column so this was to get rid of that extra column

arrond_merge.head(20) # check the last columns!



Arrondissement   Latitude  Longitude  Cluster Label 1st Most Common Venue  \
0             1st  48.864614   2.334396              4                 Hotel   
1             2nd  48.868743   2.341688              3          Cocktail Bar   
2             3rd  48.864212   2.360936              3     French Restaurant   
3             4th  48.856202   2.355619              1     French Restaurant   
4             5th  48.846059   2.344523              1     French Restaurant   
5             6th  48.850433   2.332951              0     French Restaurant   
6             7th  48.857028   2.320195              0     French Restaurant   
7             8th  48.877316   2.317261              2                 Hotel   
8             9th  48.876019   2.339962              4     French Restaurant   
9            10th  48.876106   2.359910              0           Coffee Shop   
10           11th  48.858416   2.379703              0     French Restaurant   
11           12th  48.839615   2.395752              2     French Restaurant   
12           13th  48.832397   2.355583              2     French Restaurant   
13           14th  48.833059   2.326959              3     French Restaurant   
14           15th  48.841370   2.300383              3     French Restaurant   
15           16th  48.863171   2.275765              3     French Restaurant   
16           17th  48.884224   2.322364              0     French Restaurant   
17           18th  48.890012   2.346467              0     French Restaurant   
18           19th  48.889343   2.384360              2     French Restaurant   
19           20th  48.865042   2.398929              4                   Bar   

    2nd Most Common Venue 3rd Most Common Venue 4th Most Common Venue  \
0                   Plaza         Historic Site     French Restaurant   
1       French Restaurant              Wine Bar                 Hotel   
2      Italian Restaurant             Bookstore                  Café   
3                   Plaza          Cocktail Bar   Japanese Restaurant   
4                   Plaza              Wine Bar                Bistro   
5                   Hotel                  Café           Cheese Shop   
6           Historic Site                Garden                 Plaza   
7       French Restaurant   Japanese Restaurant          Gourmet Shop   
8                  Bakery                 Hotel    Italian Restaurant   
9       French Restaurant  Cambodian Restaurant                   Bar   
10               Wine Bar                Bistro                   Bar   
11                   Park                Bakery                 Hotel   
12  Vietnamese Restaurant       Thai Restaurant    Italian Restaurant   
13                  Hotel   Japanese Restaurant    Italian Restaurant   
14                  Hotel                Bakery                Bistro   
15                  Hotel    Italian Restaurant            Art Museum   
16                  Hotel                Bistro                   Bar   
17     Italian Restaurant           Pizza Place                   Bar   
18             Restaurant             Multiplex   Japanese Restaurant   
19      French Restaurant          Cocktail Bar           Pizza Place   

   5th Most Common Venue 6th Most Common Venue  7th Most Common Venue  \
0           Cocktail Bar            Art Museum               Boutique   
1            Pizza Place          Concert Hall    Corsican Restaurant   
2                 Bakery                 Hotel         Clothing Store   
3                 Museum                 Hotel             Beer Store   
4           Dessert Shop            Restaurant         Ice Cream Shop   
5            Coffee Shop              Creperie       Department Store   
6            Pastry Shop            Art Museum       Asian Restaurant   
7     Italian Restaurant                   Bar         Clothing Store   
8    Indie Movie Theater        Scenic Lookout            Cheese Shop   
9        Thai Restaurant           Pizza Place     Chinese

#### Examining the different arrondissement clusters

##### Cluster 1

In [446]:
cluster1 = arrond_merge.loc[arrond_merge['Cluster Label'] == 0]

cluster1

Arrondissement   Latitude  Longitude  Cluster Label 1st Most Common Venue  \
5             6th  48.850433   2.332951              0     French Restaurant   
6             7th  48.857028   2.320195              0     French Restaurant   
9            10th  48.876106   2.359910              0           Coffee Shop   
10           11th  48.858416   2.379703              0     French Restaurant   
16           17th  48.884224   2.322364              0     French Restaurant   
17           18th  48.890012   2.346467              0     French Restaurant   

   2nd Most Common Venue 3rd Most Common Venue 4th Most Common Venue  \
5                  Hotel                  Café           Cheese Shop   
6          Historic Site                Garden                 Plaza   
9      French Restaurant  Cambodian Restaurant                   Bar   
10              Wine Bar                Bistro                   Bar   
16                 Hotel                Bistro                   Bar   
17    Italian Restaurant           Pizza Place                   Bar   

   5th Most Common Venue 6th Most Common Venue 7th Most Common Venue  \
5            Coffee Shop              Creperie      Department Store   
6            Pastry Shop            Art Museum      Asian Restaurant   
9        Thai Restaurant           Pizza Place    Chinese Restaurant   
10          Cocktail Bar           Pizza Place    Italian Restaurant   
16                Bakery    Italian Restaurant                 Plaza   
17                Bistro           Music Venue                Bakery   

     8th Most Common Venue 9th Most Common Venue 10th Most Common Venue  
5   Furniture / Home Store                Garden            Tailor Shop  
6                   Lounge        Chocolate Shop                  Hotel  
9                Gastropub            Taco Place                Theater  
10              Restaurant                  Park        Organic Grocery  
16                Wine Bar          Dessert Shop               Beer Bar  
17               Wine Shop           Coffee Shop             Restaurant

##### Cluster 2

In [447]:
cluster2 = arrond_merge.loc[arrond_merge['Cluster Label'] == 1]

cluster2

Arrondissement   Latitude  Longitude  Cluster Label 1st Most Common Venue  \
3            4th  48.856202   2.355619              1     French Restaurant   
4            5th  48.846059   2.344523              1     French Restaurant   

  2nd Most Common Venue 3rd Most Common Venue 4th Most Common Venue  \
3                 Plaza          Cocktail Bar   Japanese Restaurant   
4                 Plaza              Wine Bar                Bistro   

  5th Most Common Venue 6th Most Common Venue 7th Most Common Venue  \
3                Museum                 Hotel            Beer Store   
4          Dessert Shop            Restaurant        Ice Cream Shop   

  8th Most Common Venue 9th Most Common Venue 10th Most Common Venue  
3      Tapas Restaurant          Burger Joint                 Market  
4              Fountain    Seafood Restaurant               Tea Room

##### Cluster 3

In [448]:
cluster3 = arrond_merge.loc[arrond_merge['Cluster Label'] == 2]

cluster3

Arrondissement   Latitude  Longitude  Cluster Label 1st Most Common Venue  \
7             8th  48.877316   2.317261              2                 Hotel   
11           12th  48.839615   2.395752              2     French Restaurant   
12           13th  48.832397   2.355583              2     French Restaurant   
18           19th  48.889343   2.384360              2     French Restaurant   

    2nd Most Common Venue 3rd Most Common Venue 4th Most Common Venue  \
7       French Restaurant   Japanese Restaurant          Gourmet Shop   
11                   Park                Bakery                 Hotel   
12  Vietnamese Restaurant       Thai Restaurant    Italian Restaurant   
18             Restaurant             Multiplex   Japanese Restaurant   

   5th Most Common Venue 6th Most Common Venue 7th Most Common Venue  \
7     Italian Restaurant                   Bar        Clothing Store   
11                 Plaza    Italian Restaurant                   Bar   
12                  Café                 Hotel                   Bar   
18                Bistro                  Café          Concert Hall   

   8th Most Common Venue 9th Most Common Venue 10th Most Common Venue  
7                   Park        Cosmetics Shop            Art Gallery  
11                Garden        Farmers Market                 Bistro  
12                Bakery                  Park            Supermarket  
18                   Bar                  Park            Pizza Place

##### Cluster 4

In [449]:
cluster4 = arrond_merge.loc[arrond_merge['Cluster Label'] == 3]

cluster4

Arrondissement   Latitude  Longitude  Cluster Label 1st Most Common Venue  \
1             2nd  48.868743   2.341688              3          Cocktail Bar   
2             3rd  48.864212   2.360936              3     French Restaurant   
13           14th  48.833059   2.326959              3     French Restaurant   
14           15th  48.841370   2.300383              3     French Restaurant   
15           16th  48.863171   2.275765              3     French Restaurant   

   2nd Most Common Venue 3rd Most Common Venue 4th Most Common Venue  \
1      French Restaurant              Wine Bar                 Hotel   
2     Italian Restaurant             Bookstore                  Café   
13                 Hotel   Japanese Restaurant    Italian Restaurant   
14                 Hotel                Bakery                Bistro   
15                 Hotel    Italian Restaurant            Art Museum   

   5th Most Common Venue 6th Most Common Venue 7th Most Common Venue  \
1            Pizza Place          Concert Hall   Corsican Restaurant   
2                 Bakery                 Hotel        Clothing Store   
13                Bistro              Creperie                   Bar   
14  Gym / Fitness Center                 Plaza     Korean Restaurant   
15                Bakery                 Plaza             Hotel Bar   

   8th Most Common Venue  9th Most Common Venue 10th Most Common Venue  
1            Candy Store                 Museum    Szechuan Restaurant  
2           Cocktail Bar    Japanese Restaurant         Sandwich Place  
13          Dessert Shop  Vietnamese Restaurant                 Museum  
14    Italian Restaurant                   Park    Lebanese Restaurant  
15  Gym / Fitness Center                 Garden                 Museum

##### Cluster 5

In [450]:
cluster5 = arrond_merge.loc[arrond_merge['Cluster Label'] == 4]

cluster5

Arrondissement   Latitude  Longitude  Cluster Label 1st Most Common Venue  \
0             1st  48.864614   2.334396              4                 Hotel   
8             9th  48.876019   2.339962              4     French Restaurant   
19           20th  48.865042   2.398929              4                   Bar   

   2nd Most Common Venue 3rd Most Common Venue 4th Most Common Venue  \
0                  Plaza         Historic Site     French Restaurant   
8                 Bakery                 Hotel    Italian Restaurant   
19     French Restaurant          Cocktail Bar           Pizza Place   

   5th Most Common Venue 6th Most Common Venue  7th Most Common Venue  \
0           Cocktail Bar            Art Museum               Boutique   
8    Indie Movie Theater        Scenic Lookout            Cheese Shop   
19                Bakery    Italian Restaurant  Vietnamese Restaurant   

   8th Most Common Venue 9th Most Common Venue 10th Most Common Venue  
0     Italian Restaurant                Garden           Dessert Shop  
8         Chocolate Shop                Church           Cocktail Bar  
19           Music Venue   Moroccan Restaurant     Mexican Restaurant

In [451]:
## run K-means to cluster the landmarks into 5 clusters

# set number of clusters
kclusters = 8

landmark_clustering = landmarks_df.drop('Landmark', 1)

# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(landmark_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_[0:20]

array([0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 4, 0, 0, 0, 6, 0, 0, 0, 0, 0],
      dtype=int32)

#### Create a dataframe with the clusters and landmarks

#### Looking at the results, it's not very useful because there aren't really any distinct clusters. I will have to manually group these landmarks together when I create the travel itinerary

In [452]:
# add clustering labels

#landmarks_df.insert(0, 'Cluster Label', kmeans.labels_)

landmarks_merge = landmarks_df

landmarks_merge = landmarks_merge.drop('Cluster',1) # accidentally added added another cluster column so this was to get rid of that extra column

landmarks_merge = landmarks_merge.sort_values(['Cluster Label'], ascending=False)

landmarks_merge


Cluster Label                        Landmark   Latitude  Longitude
26              7            Palace of Versailles  48.804425   2.120285
29              6                Disneyland Paris  48.871136   2.776127
10              5                  Picasso Museum  41.385107   2.181205
24              4                      Montmartre  46.802135  -0.719894
14              3                  Hôtel de Ville  43.949297   4.805260
32              2                    Rodin Museum  39.961929 -75.173951
30              1            Place de la Concorde  29.900205 -90.009515
23              0            Palais du Luxembourg  48.848528   2.336836
25              0                  Champs-Élysées  48.870757   2.305331
27              0                Tuileries Garden  48.863662   2.326839
28              0                    Moulin Rouge  48.884079   2.332408
0               0  Cathédrale Notre-Dame de Paris  48.852937   2.350051
21              0           Philharmonie de Paris  48.891921   2.394139
31              0              Catacombs of Paris  48.833964   2.332492
33              0                  Île de la Cité  48.854705   2.347485
34              0                Orangerie Museum  48.863765   2.322660
35              0                   Pont des Arts  48.857811   2.337246
36              0                 Île Saint-Louis  48.851613   2.356734
37              0                   Place Vendôme  48.867463   2.329428
38              0             Saint-Jacques Tower  48.858003   2.348922
22              0                   Musée d’Orsay  48.859918   2.326583
20              0             The Palais de Tokyo  48.863990   2.296522
1               0                 Arc de Triomphe  48.873779   2.295037
19              0                  Île de la Cité  48.854705   2.347485
2               0                 Centre Pompidou  48.860592   2.352474
3               0             Sacré-Cœur Basilica  48.886806   2.343015
4               0                    Eiffel Tower  48.858260   2.294499
5               0                      The Louvre  48.861147   2.338028
6               0                 La Grande Arche  48.893015   2.237621
7               0                   Les Invalides  48.857037   2.311878
8               0         Fondation Louis Vuitton  48.876650   2.263338
9               0                        Panthéon  48.845419   2.352584
11              0          Cinémathèque Française  48.836999   2.382635
12              0                   Opéra Garnier  48.872031   2.331790
13              0                The Grand Palais  48.866161   2.312223
15              0               Fondation Cartier  48.837318   2.331932
16              0                    Jeu de Paume  48.865816   2.324088
17              0              Jardin des Plantes  48.843222   2.359509
18              0  Fondation Jerôme Seydoux-Pathé  48.833477   2.354907
39              0                 La Conciergerie  48.855949   2.346026

#### Printing the full list of venues below

In [487]:
arrond_venues

Arrondissement  Arrondissement Latitude  Arrondissement Longitude  \
0               1st                48.864614                  2.334396   
1               1st                48.864614                  2.334396   
2               1st                48.864614                  2.334396   
3               1st                48.864614                  2.334396   
4               1st                48.864614                  2.334396   
5               1st                48.864614                  2.334396   
6               1st                48.864614                  2.334396   
7               1st                48.864614                  2.334396   
8               1st                48.864614                  2.334396   
9               1st                48.864614                  2.334396   
10              1st                48.864614                  2.334396   
11              1st                48.864614                  2.334396   
12              1st                48.864614                  2.334396   
13              1st                48.864614                  2.334396   
14              1st                48.864614                  2.334396   
15              1st                48.864614                  2.334396   
16              1st                48.864614                  2.334396   
17              1st                48.864614                  2.334396   
18              1st                48.864614                  2.334396   
19              1st                48.864614                  2.334396   
20              1st                48.864614                  2.334396   
21              1st                48.864614                  2.334396   
22              1st                48.864614                  2.334396   
23              1st                48.864614                  2.334396   
24              1st                48.864614                  2.334396   
25              1st                48.864614                  2.334396   
26              1st                48.864614                  2.334396   
27              1st                48.864614                  2.334396   
28              1st                48.864614                  2.334396   
29              1st                48.864614                  2.334396   
30              1st                48.864614                  2.334396   
31              1st                48.864614                  2.334396   
32              1st                48.864614                  2.334396   
33              1st                48.864614                  2.334396   
34              1st                48.864614                  2.334396   
35              1st                48.864614                  2.334396   
36              1st                48.864614                  2.334396   
37              1st                48.864614                  2.334396   
39              1st                48.864614                  2.334396   
40              1st                48.864614                  2.334396   
41              1st                48.864614                  2.334396   
42              1st                48.864614                  2.334396   
43              1st                48.864614                  2.334396   
44              1st                48.864614                  2.334396   
45              1st                48.864614                  2.334396   
46              1st                48.864614                  2.334396   
47              1st                48.864614                  2.334396   
48              1st                48.864614                  2.334396   
49              1st                48.864614                  2.334396   
50              1st                48.864614                  2.334396   
51              1st                48.864614                  2.334396   
52              1st                48.864614                  2.334396   
53              1st                48.864614                  2.334396   
54       

#### I'm going to create separate dataframes for different categories below so it'll be easier to call when I create maps to display different activities

In [489]:
# Things to Do
museum = arrond_venues.loc[arrond_venues['Venue Category'].isin(['Museum','Art Museum', 'Science Museum', 'Exhibit', 'Art Gallery', 'History Museum'])]

outdoor_sights = arrond_venues.loc[arrond_venues['Venue Category'].isin(['Bridge', 'Street Art','Plaza', 'Pedestrian Plaza', 'Scenic Lookout', 'Outdoor Sculpture', 'Theme Park Ride / Attraction', 'Canal', 'Park', 'Garden', 'Botanical Garden' ])]
                                   
fashion_store = arrond_venues.loc[arrond_venues['Venue Category'].isin(['Department Store','Boutique',"Men's Store","Women's Store",'Cosmetics Shop', 'Clothing Store', 'Jewelry Store', 'Tailor Shop', 'Gift Shop', 'Shopping Mall'])]

night_life = arrond_venues.loc[arrond_venues['Venue Category'].isin(['Nightclub', 'Hookah Bar', 'Jazz Club', 'Rock Club'])]

bike = arrond_venues.loc[arrond_venues['Venue Category'] == 'Bike Rental / Bike Share']                                   

relax = arrond_venues.loc[arrond_venues['Venue Category'].isin(['Spa', 'Massage Studio'])]


# Things to Eat and Drink
asian_food = arrond_venues.loc[arrond_venues['Venue Category'].isin(['Udon Restaurant', 'Japanese Restaurant', 'Asian Restaurant', 
                                                                     'Szechuan Restaurant', 'Korean Restaurant', 'Vietnamese Restaurant',
                                                                    'Thai Restaurant', 'Cambodian Restaurant', 'Sushi Restaurant',
                                                                    'Jiangxi Restaurant', 'Chinese Restaurant', 'Indian Restaurant'])]

world_food = arrond_venues.loc[arrond_venues['Venue Category'].isin(['Modern European Restaurant', 'Italian Restaurant', 'Argentinian Restaurant', 'American Restaurant', 'Scandinavian Restaurant', 'Trattoria/Osteria' , 
                                                                     'Israeli Restaurant', 'Vegetarian / Vegan Restaurant', 'Seafood Restaurant', 'Lebanese Restaurant', 'Ethiopian Restaurant', 'Mexican Restaurant',
                                                                    'Breton Restaurant','Corsican Restaurant', 'Mediterranean Restaurant', 'Russian Restaurant', 'Tapas Restaurant', 'Falafel Restaurant', 'Moroccan Restaurant',
                                                                    'Turkish Restaurant', 'Portuguese Restaurant', 'Greek Restaurant', 'Brazilian Restaurant', 'Peruvian Restaurant', 'Comfort Food Restaurant', 'Steakhouse',
                                                                    'Basque Restaurant', 'Middle Eastern Restaurant', 'Arepa Restaurant', 'Southern / Soul Food Restaurant', 'African Restaurant', 'Gluten-free Restaurant'])]
                               
french = arrond_venues.loc[arrond_venues['Venue Category'].isin(['French Restaurant', 'Creperie','Cheese Shop', 'Provençal Restaurant', 'Bistro', 'Brasserie', 'Auvergne Restaurant'])]

dessert = arrond_venues.loc[arrond_venues['Venue Category'].isin(['Ice Cream Shop','Pastry Shop', 'Bakery', 'Dessert Shop', 'Donut Shop', 'Chocolate Shop', 'Cupcake Shop'])] 
                           
drink = arrond_venues.loc[arrond_venues['Venue Category'].isin(['Cocktail Bar', 'Beer Bar','Beer Store', 'Roof Deck', 'Wine Bar', 'Tea Room', 'Liquor Store', 'Wine Shop', 
                                                                'Bar', 'Gastropub', 'Speakeasy', 'Lounge', 'Beer Garden', 'Irish Pub', 'Champagne Bar', 'Hotel Bar', 'Vineyard'])]
cafe = arrond_venues.loc[arrond_venues['Venue Category'].isin(['Café', 'Breakfast Spot', 'Coffe Shop', 'Tea Room'])]
                          
fast_food = arrond_venues.loc[arrond_venues['Venue Category'].isin(['Burger Joint', 'Hot Dog Joint', 'Sandwich Place', 'Pizza Place', 
                                                                    'Fish & Chips Shop', 'Deli / Bodega', 'Taco Place', 'Food & Drink Shop',
                                                                   'BBQ Joint', 'Bagel Shop', 'Fast Food Restaurant', 'Diner', 'Food Truck'])]                 

market = arrond_venues.loc[arrond_venues['Venue Category'].isin(['Farmers Market','Cheese Shop', 'Organic Grocery', 'Market', 'Supermarket'])]


# Things to See
historic_site = arrond_venues.loc[arrond_venues['Venue Category'].isin(['Historic Site', 'Monument / Landmark'])]


# Things to hear
perform = arrond_venues.loc[arrond_venues['Venue Category'].isin(['Theater', 'Indie Movie Theater', 'Opera House', 'Comedy Club', 'Concert Hall', 'Music Venue', 'Performing Arts Venue'])]                 


# Places to live 
lodging = arrond_venues.loc[arrond_venues['Venue Category'].isin(['Hotel', 'Hostel'])]

#### The following function shows venues as points along with points designating arrondissement

In [480]:
# create a map of Paris

def map_with_arrond_and_points(points_df, arrondll):

    map_name = folium.Map(location = [48.8566101, 2.3514992], zoom_start = 12)
    
    map_name.choropleth(
        geo_data=paris,
        data=pop_2005,
        columns=['Arrondissement', 'Population'],
        key_on='feature.properties.nom',
        fill_color='PuBu', 
        fill_opacity=0.1, 
        line_opacity=0.5,)

#add points of interest markers to the Paris map
    for lat, long, points, cat in zip(points_df['Venue Latitude'], points_df['Venue Longitude'], 
                                 points_df['Venue'], points_df['Venue Category']):
        label = '{}, {}'.format(points, cat)
        label = folium.Popup(label, parse_html=True)
        folium.CircleMarker(
            [lat, long],
            radius = 7, 
            popup = label,
            color = 'yellow',
            fill = True,
            fill_color = 'blue',
            fill_opacity = 0.7,
            parse_html = False).add_to(map_name)
        
#add arrond markers to the Paris map
    for lat, long, arrond in zip(arrondll['Latitude'], arrondll['Longitude'], 
                                 arrondll['Arrondissement']):
        label = '{}'.format(arrond)
        label = folium.Popup(label, parse_html=True)
        folium.CircleMarker(
            [lat, long],
            radius = 5, 
            popup = label,
            color = 'white',
            fill = True,
            fill_color = 'green',
            fill_opacity = 0.5,
            parse_html = False).add_to(map_name)
        
        
    return map_name

#### This shows French Restaurants

In [455]:
map_with_arrond_and_points(points_df = french, arrondll = arrond_LL)

#### This shows French cafés (including cafés, coffee shops, breakfast spots)

In [488]:
map_with_arrond_and_points(points_df = cafe, arrondll = arrond_LL)

#### The following function shows venues as clusters along with points designating arrondissement

In [456]:
def map_with_arrond_and_points_v1(points_df, arrondll):

# Add the boundaries of the arrondissement
    map_name = folium.Map(location = [48.8566101, 2.3514992], zoom_start = 12)
    
    map_name.choropleth(
        geo_data=paris,
        data=pop_2005,
        columns=['Arrondissement', 'Population'],
        key_on='feature.properties.nom',
        fill_color='PuBu', 
        fill_opacity=0.1, 
        line_opacity=0.5,)

    # instantiate a mark cluster object for the incidents in the dataframe
    venues = plugins.MarkerCluster().add_to(map_name)

    # loop through the dataframe and add each data point to the mark cluster
    for lat, lng, name, cat in zip(points_df['Venue Latitude'], points_df['Venue Longitude'], 
                                 points_df['Venue'], points_df['Venue Category']):
        label = '{}, {}'.format(name, cat)
        label = folium.Popup(label, parse_html=True)
        folium.Marker(
            location=[lat, lng],
            icon=None,
            popup=label).add_to(venues)
        
        
#add arrond markers to the Paris map
    for lat, long, arrond in zip(arrondll['Latitude'], arrondll['Longitude'], 
                                 arrondll['Arrondissement']):
        label = '{}'.format(arrond)
        label = folium.Popup(label, parse_html=True)
        folium.CircleMarker(
            [lat, long],
            radius = 5, 
            popup = label,
            color = 'white',
            fill = True,
            fill_color = 'green',
            fill_opacity = 0.5,
            parse_html = False).add_to(map_name)
        
    return map_name

 


#### This is a function for a map showing the major landmarks of Paris along with the nearby venues in clusters

In [457]:
def map_with_arrond_and_points_v2(points_df, arrondll, landmarks):

# Add the boundaries of the arrondissement
    map_name = folium.Map(location = [48.8566101, 2.3514992], zoom_start = 12)
    
    map_name.choropleth(
        geo_data=paris,
        data=pop_2005,
        columns=['Arrondissement', 'Population'],
        key_on='feature.properties.nom',
        fill_color='PuBu', 
        fill_opacity=0.1, 
        line_opacity=0.5,)

    # instantiate a mark cluster object for the incidents in the dataframe
    venues = plugins.MarkerCluster().add_to(map_name)

    # loop through the dataframe and add each data point to the mark cluster
    for lat, lng, name, cat in zip(points_df['Venue Latitude'], points_df['Venue Longitude'], 
                                 points_df['Venue'], points_df['Venue Category']):
        label = '{}, {}'.format(name, cat)
        label = folium.Popup(label, parse_html=True)
        folium.Marker(
            location=[lat, lng],
            icon=None,
            popup=label).add_to(venues)
        
        
#add arrond markers to the Paris map
    for lat, long, arrond in zip(arrondll['Latitude'], arrondll['Longitude'], 
                                 arrondll['Arrondissement']):
        label = '{}'.format(arrond)
        label = folium.Popup(label, parse_html=True)
        folium.CircleMarker(
            [lat, long],
            radius = 5, 
            popup = label,
            color = 'white',
            fill = True,
            fill_color = 'green',
            fill_opacity = 0.5,
            parse_html = False).add_to(map_name)
        
#add landmarks of interest markers to the Paris map
    for lat, long, landmark in zip(landmarks['Latitude'], landmarks['Longitude'], 
                                 landmarks['Landmark']):
        label = '{}'.format(landmark)
        label = folium.Popup(label, parse_html=True)
        folium.CircleMarker(
            [lat, long],
            radius = 7, 
            popup = label,
            color = 'red',
            fill = True,
            fill_color = 'blue',
            fill_opacity = 0.7,
            parse_html = False).add_to(map_name)
        
    return map_name


#### Here's a map with clusters of French restaurants around famous landmarks

In [458]:
map_with_arrond_and_points_v2(points_df = french, arrondll = arrond_LL, landmarks = landmarks_df)

#### Here's a map of clusters of musuems and their proximity to famous landmarks

In [483]:
map_with_arrond_and_points_v2(points_df = museum, arrondll = arrond_LL, landmarks = landmarks_df)

#### Here's a map showing the local markets and their proximity to famous landmarks

In [490]:
map_with_arrond_and_points_v2(points_df = market, arrondll = arrond_LL, landmarks = landmarks_df)

#### Got a sweet tooth? Here's a cluster of dessert places near famous landmarks

In [460]:
map_with_arrond_and_points_v2(points_df = dessert, arrondll = arrond_LL, landmarks = landmarks_df)

#### Need some rest after a long day of exploring? Here are some lodging options

In [461]:
map_with_arrond_and_points_v2(points_df = lodging, arrondll = arrond_LL, landmarks = landmarks_df)

#### Here are some historical sites near famous landmarks

In [462]:
map_with_arrond_and_points_v1(points_df = historic_site, arrondll = arrond_LL)

#### Here are some outdoor sights (aka parks, gardens, plazas, scenic viewpoints etc)

In [484]:
map_with_arrond_and_points_v1(points_df = outdoor_sights, arrondll = arrond_LL)

#### Here's a map of night life venues near famous landmarks (clubs, etc)

In [491]:
map_with_arrond_and_points_v2(points_df = night_life, arrondll = arrond_LL, landmarks = landmarks_df)

#### Here's a map of bars, liquor stores, cocktail lounges, etc and their proximity from famous landmarks

In [492]:
map_with_arrond_and_points_v2(points_df = drink, arrondll = arrond_LL, landmarks = landmarks_df)

#### Here's a map of cafés and their proximity to famous landmarks

In [467]:
map_with_arrond_and_points_v2(points_df = cafe, arrondll = arrond_LL, landmarks = landmarks_df)

#### Here's a map of fast food establishments (pizza, burgers, hot dog) and their proximity to famous landmarks

In [468]:
map_with_arrond_and_points_v2(points_df = fast_food, arrondll = arrond_LL, landmarks = landmarks_df)

#### Here's a map of bars, cocktail lounges, etc point by point (not clustered)

In [481]:
map_with_arrond_and_points(drink, arrond_LL)

#### Here's a map of stores, boutiques, shops etc by point (not clustered)

In [485]:
map_with_arrond_and_points(fashion_store, arrond_LL)

#### Here's a map of global food options (all other foods besides fast food and French cuisine) and their proximity to famous landmarks

In [486]:
map_with_arrond_and_points_v2(points_df = world_food, arrondll = arrond_LL, landmarks = landmarks_df)

#### Here's a map of performance venues (opera houses, theaters, music venues etc) and their proximity to famous landmarks

In [495]:
map_with_arrond_and_points_v2(points_df = perform, arrondll = arrond_LL, landmarks = landmarks_df)